In [1]:
import pandas as pd
import os
import sys
import numpy as np
import shutil
import glob

# suppress pandas purely educational warnings
from warnings import simplefilter
simplefilter(action="ignore", category=pd.errors.PerformanceWarning)

sys.path.append(os.path.expanduser('../../'))
from scripts.utils.file_helpers import pull_csv_from_directory, upload_csv_aws
from scripts.utils.write_metadata import append_metadata

In [2]:
# pull csv from aws
bucket_name = 'ca-climate-index'
aws_dir = '3_fair_data/index_data/'

pull_csv_from_directory(bucket_name, aws_dir, search_zipped=False)

Saved DataFrame as 'built_housing_median_age_metric.csv'
Saved DataFrame as 'built_housing_mobile_homes_metric.csv'
Saved DataFrame as 'built_housing_quality_metric.csv'
Saved DataFrame as 'built_metric_housing_vacancy_metric.csv'
Saved DataFrame as 'built_power_plant_metric.csv'
Saved DataFrame as 'climate_wildfire_redbooks_loss_metric.csv'
Saved DataFrame as 'climate_wildfire_redbooks_loss_metric_buildings.csv'
Saved DataFrame as 'climate_wildfire_redbooks_loss_metric_fatalities.csv'
Saved DataFrame as 'governance_emergency_management_metric.csv'
Saved DataFrame as 'governance_hazard_mitigation_metric.csv'
Saved DataFrame as 'natural_air_quality_metric.csv'
Saved DataFrame as 'society_ambulatory_disability_metric.csv'
Saved DataFrame as 'society_american_indian_alaska_native_metric.csv'
Saved DataFrame as 'society_cognitive_disability_metric.csv'
Saved DataFrame as 'society_financial_assistance_metric.csv'
Saved DataFrame as 'society_food_access_metric.csv'
Saved DataFrame as 'societ

In [3]:
# Define the output folder path
output_folder = 'output_folder'

# Create the output folder if it doesn't exist
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

# Find all CSV files starting with 'society_'
source_files = [file for file in glob.glob('society_*.csv') if 'social' not in file]

# Iterate through the source files and copy only CSV files to the output folder
for file in source_files:
    # Construct the destination file path
    destination_path = os.path.join(output_folder, os.path.basename(file))
    
    # Copy the file to the output folder
    shutil.copyfile(file, destination_path)
    
    # Remove the original file
    os.remove(file)

print(f"Copied and removed {len(source_files)} CSV files.")

# Delete all CSV files in the current directory that are not in the output folder
current_files = glob.glob('*.csv')
for file in current_files:
    if file not in [os.path.basename(f) for f in source_files]:
        os.remove(file)

print(f"Deleted {len(current_files) - len(source_files)} local CSV files.")


Copied and removed 21 CSV files.
Deleted 3 local CSV files.


In [4]:
# Define the output folder path
output_folder = 'output_folder'

# Get a list of all CSV files in the output folder
csv_files = glob.glob(os.path.join(output_folder, '*.csv'))

# Initialize an empty DataFrame for merging
merged_df = pd.DataFrame()
# Iterate through each CSV file and merge them on the 'census_tract' column
for file in csv_files:
    # Read the CSV file into a DataFrame
    df = pd.read_csv(file)
    
    # Keep only the 'census_tract' and the last column from each file
    last_column = df.columns[-1]
    df = df[['census_tract', last_column]]
    
    # Merge the DataFrame with the existing merged DataFrame
    if merged_df.empty:
        merged_df = df
    else:
        merged_df = pd.merge(merged_df, df, on='census_tract', how='outer')

# Save the merged DataFrame to a CSV file
merged_df.to_csv('concatenate_society_economy_metrics.csv', index=False)

print(f"Merged CSV saved as concatenate_society_economy_metrics.csv")

Merged CSV saved as concatenate_society_economy_metrics.csv


In [7]:
society_economy_metrics = pd.read_csv('concatenate_society_economy_metrics.csv')
society_economy_metrics

census_tract  percent_population_ambulatory_disabilities  \
0     6.001400e+09                                    4.680330   
1     6.001400e+09                                    4.005589   
2     6.001400e+09                                    2.295782   
3     6.001400e+09                                    3.646564   
4     6.001400e+09                                    3.367941   
...            ...                                         ...   
9125  6.115041e+09                                    8.387800   
9126  6.115041e+09                                    9.160082   
9127  6.115041e+09                                   16.826923   
9128  6.115041e+09                                   12.277228   
9129           NaN                                         NaN   

     percent_total_pop_american_indian_alaska_native  \
0                                                0.0   
1                                                0.4   
2                                                0.5   
3                                                0.5   
4                                                0.1   
...                                              ...   
9125                                             0.3   
9126                                             2.6   
9127                                             1.1   
9128                                             0.0   
9129                                             NaN   

      percent_population_cognitive_disabilities  \
0                                      5.170005   
1                                      1.904253   
2                                      3.529687   
3                                      3.165358   
4                                      6.219631   
...                                         ...   
9125                                   3.745976   
9126                                   9.702797   
9127                                   9.405941   
9128                                        NaN   
9129                                        NaN   

      percent_children_household_financial_assistance  \
0                                           15.885023   
1                                            0.000000   
2                                            3.184713   
3                                           14.240170   
4                                            4.435484   
...                                               ...   
9125                                         0.000000   
9126                                         0.000000   
9127                                        44.331984   
9128                                        42.857143   
9129                                              NaN   

      percent_1miurban_10mirural  real_percent_total_pop_over_65  \
0                      58.256725                       27.041909   
1                      30.832177                       25.756870   
2                      30.832177                       16.301833   
3                      30.832177                       12.856475   
4                      30.832177                       16.434540   
...                          ...                             ...   
9125                   37.636696                       33.605664   
9126                   37.636696                       29.997073   
9127                   37.636696                       20.891608   
9128                   37.636696                       53.960396   
9129                         NaN                             NaN   

     percent_total_pop_under_5  \
0                          4.1   
1                          7.9   
2                          2.3   
3                          7.5   
4                          4.0   
...                        ...   
9125                       6.9   
9126                       2.6   
9127                       2.7   
9128                       4.9   
9129                       NaN   

      asthma_rel

In [6]:
import pandas as pd
import numpy as np

def handle_outliers(df, output_csv):
    # Columns to process (exclude 'census_tract')
    columns_to_process = [col for col in df.columns if col != 'census_tract']
    
    # Dictionary to store counts of adjusted rows
    adjusted_counts = {}

    for column in columns_to_process:
        # Convert the column to numeric, forcing any errors to NaN
        df[column] = pd.to_numeric(df[column], errors='coerce')
        
        Q1 = df[column].quantile(0.25)
        Q3 = df[column].quantile(0.75)
        IQR = Q3 - Q1

        if IQR == 0:
            print(f"Column '{column}' has no IQR (Q1 == Q3). Skipping outlier handling for this column.")
            continue

        max_fence = Q3 * 3
        min_fence = Q1 * -3

        print(f'For column {column}:')
        print(f'  Q1 (25th percentile): {Q1}')
        print(f'  Q3 (75th percentile): {Q3}')
        print(f'  IQR: {IQR}')
        print(f'  Max fence: {max_fence}')
        print(f'  Min fence: {min_fence}')

        # Identify outliers
        outliers = df[(df[column] > max_fence) | (df[column] < min_fence)]
        
        # Print outliers and their corresponding 'census_tract'
        if not outliers.empty:
            print(f"Outliers detected in column '{column}':")
            for _, row in outliers.iterrows():
                print(f"census_tract: {row['census_tract']}, value: {row[column]}")

        # Count the number of adjustments
        count_adjusted = df[(df[column] > max_fence) | (df[column] < min_fence)].shape[0]
        adjusted_counts[column] = count_adjusted
        
        # Clip the outliers
        df[column] = df[column].clip(lower=min_fence, upper=max_fence)
    
    # Save the updated DataFrame back to CSV
    df.to_csv(output_csv, index=False)
    
    # Print the adjusted counts
    print("Number of rows adjusted per column:")
    for column, count in adjusted_counts.items():
        print(f"  {column}: {count}")

    return df

# Handle outliers
handle_outlier_csv = 'no_outlier_society_economy_metrics.csv'
no_outlier_society_economy_metrics = handle_outliers(society_economy_metrics, handle_outlier_csv)
print(f"Processed and saved {handle_outlier_csv} with outlier handling.")

For column percent_population_ambulatory_disabilities:
  Q1 (25th percentile): 3.4249678882757117
  Q3 (75th percentile): 7.035102433873741
  IQR: 3.610134545598029
  Max fence: 21.105307301621224
  Min fence: -10.274903664827136
Outliers detected in column 'percent_population_ambulatory_disabilities':
census_tract: 6013351105.0, value: 21.223814773980155
census_tract: 6025012400.0, value: 21.39219015280136
census_tract: 6033000601.0, value: 22.210690192008304
census_tract: 6037125322.0, value: 21.15093387178193
census_tract: 6037206301.0, value: 31.129864041256443
census_tract: 6037206302.0, value: 25.71554381329811
census_tract: 6037206303.0, value: 28.146536089952846
census_tract: 6037302201.0, value: 22.377807133421403
census_tract: 6037310701.0, value: 22.231614539306847
census_tract: 6037980014.0, value: 48.888888888888886
census_tract: 6037980021.0, value: 23.52941176470588
census_tract: 6039000111.0, value: 21.643109540636043
census_tract: 6059021813.0, value: 84.61538461538461

In [8]:
def handle_outliers(df, output_csv):
    # Columns to process (exclude 'census_tract')
    columns_to_process = [col for col in df.columns if col != 'census_tract']
    
    # Dictionary to store counts of adjusted rows
    adjusted_counts = {}

    for column in columns_to_process:
        # Convert the column to numeric, forcing any errors to NaN
        df[column] = pd.to_numeric(df[column], errors='coerce')
        
        Q1 = df[column].quantile(0.25)
        Q3 = df[column].quantile(0.75)
        IQR = Q3 - Q1

        if IQR == 0:
            print(f"Column '{column}' has no IQR (Q1 == Q3). Skipping outlier handling for this column.")
            continue

        max_fence = (Q3 + 1.5) * IQR
        min_fence = (Q1 - 1.5) * IQR

        print(f'For column {column}:')
        print(f'  Q1 (25th percentile): {Q1}')
        print(f'  Q3 (75th percentile): {Q3}')
        print(f'  IQR: {IQR}')
        print(f'  Max fence: {max_fence}')
        print(f'  Min fence: {min_fence}')

        # Identify outliers
        outliers = df[(df[column] > max_fence) | (df[column] < min_fence)]
        
        # Print outliers and their corresponding 'census_tract'
        if not outliers.empty:
            print(f"Outliers detected in column '{column}':")
            for _, row in outliers.iterrows():
                print(f"census_tract: {row['census_tract']}, value: {row[column]}")

        # Count the number of adjustments
        count_adjusted = df[(df[column] > max_fence) | (df[column] < min_fence)].shape[0]
        adjusted_counts[column] = count_adjusted
        
        # Clip the outliers
        df[column] = df[column].clip(lower=min_fence, upper=max_fence)
    
    # Save the updated DataFrame back to CSV
    df.to_csv(output_csv, index=False)
    
    # Print the adjusted counts
    print("Number of rows adjusted per column:")
    for column, count in adjusted_counts.items():
        print(f"  {column}: {count}")

    return df

# Handle outliers
handle_outlier_csv = 'no_outlier_society_economy_metrics.csv'
no_outlier_society_economy_metrics = handle_outliers(society_economy_metrics, handle_outlier_csv)
print(f"Processed and saved {handle_outlier_csv} with outlier handling.")

For column percent_population_ambulatory_disabilities:
  Q1 (25th percentile): 3.4249678882757117
  Q3 (75th percentile): 7.035102433873741
  IQR: 3.610134545598029
  Max fence: 30.81286814674541
  Min fence: 6.949393072631034
Outliers detected in column 'percent_population_ambulatory_disabilities':
census_tract: 6001400100.0, value: 4.680330376261853
census_tract: 6001400200.0, value: 4.005589194224499
census_tract: 6001400300.0, value: 2.2957821676454886
census_tract: 6001400400.0, value: 3.64656381486676
census_tract: 6001400500.0, value: 3.367941250949608
census_tract: 6001400600.0, value: 4.13022351797862
census_tract: 6001400700.0, value: 5.947877259352669
census_tract: 6001400800.0, value: 4.129181084198385
census_tract: 6001400900.0, value: 1.160337552742616
census_tract: 6001401000.0, value: 5.448462641389199
census_tract: 6001401100.0, value: 3.9010294383240014
census_tract: 6001401200.0, value: 1.3360053440213762
census_tract: 6001401300.0, value: 2.625868055555556
census_tr

### Testing with one csv